# Roads / shapes equivalence for Big Blue Bus

Create a version of `shapes` that is based on roads, where we retain the coordinate order of the bus's path, but can link more closely to roads.

Keep the benefits of `shapes`, which is the transit path, while decreasing its limitations, such as instability when we pull out the timeline (after a couple months, `shape_id` changes, even though its path is roughly equivalent). We also aren't able to aggregate across many trips within the same operator, even if they share the majority of the path, with slight deviations. It further falls apart when we try to find operators who may travel for a very short period on a major boulevard.

We need an equivalence in bringing in roads. Without `shapes`, it's hard for us to understand the order of road segments the bus is traveling on, especially as it makes turns on the road network. We need the order that `shapes` provides so we can project a vehicle position and fit that into the broader trip / transit path context.

In [1]:
import folium
import geopandas as gpd
import pandas as pd
import shapely

from shared_utils import geo_utils, rt_dates, rt_utils
from segment_speed_utils import helpers
from segment_speed_utils.project_vars import SHARED_GCS, PROJECT_CRS

import sys
sys.path.append("scripts/")
import cut_road_segments

analysis_date = rt_dates.DATES["oct2024"]

In [2]:
def buffer_shapes(shapes, buffer_meters):
    """
    TODO: notes on what buffer size we need...play around
    with the threshold to capture as much of the roads
    as we need while trying to minimize all the side streets.
    """
    shapes_buff = shapes.assign(
        geometry = shapes.geometry.buffer(buffer_meters)
    )
    
    return shapes_buff


trips = helpers.import_scheduled_trips(
    analysis_date,
    filters = [[
        ("name", "in", ["Big Blue Bus Schedule"]),
    ]],
    columns = ["shape_array_key"],
    get_pandas = True
)

shapes = helpers.import_scheduled_shapes(
    analysis_date,
    columns = ["shape_array_key", "geometry"],
    filters = [[("shape_array_key", "in", trips.shape_array_key)]],
    get_pandas = True
).to_crs(PROJECT_CRS)

In [3]:
caltrans_district = gpd.read_parquet(
    f"{SHARED_GCS}caltrans_districts.parquet",
    filters = [[("DISTRICT", "==", 7)]],
    columns = ["DISTRICT", "geometry"]
).to_crs(PROJECT_CRS)


def spatial_join_to_district(
    gdf: gpd.GeoDataFrame, 
    caltrans_district: gpd.GeoDataFrame
):
    """
    Release this filter when we move out of 1 operator.
    """
    keep_cols = gdf.columns
    
    gdf2 = gpd.sjoin(
        gdf,
        caltrans_district,
        how = "inner",
        predicate = "intersects"
    )[keep_cols]
    
    return gdf2

In [4]:
# Modify cut_road_segments and use this
def add_segment_direction_vector(df: gpd.GeoDataFrame) -> gpd.GeoDataFrame:
    """
    Instead of using primary direction, let's get direction vector
    and see if dot products help us filter out 
    the extraneous side streets.
    """
    df = df.dropna(subset="geometry")
    df = rt_utils.add_origin_destination(df)
    
    x_dir, y_dir = geo_utils.get_direction_vector(df.origin, df.destination)
    x_norm, y_norm = geo_utils.get_normalized_vector((x_dir, y_dir))

    df2 = df.assign(
        x_norm = x_norm,
        y_norm = y_norm
    ).drop(columns = ["origin","destination"])

    return df2

In [5]:
segmented_roads = gpd.read_parquet(
    f"{SHARED_GCS}segmented_roads_100m_2020.parquet",
    columns = ["linearid", "mtfcc", "fullname", "segment_sequence", "geometry"]
).to_crs(PROJECT_CRS).pipe(
    spatial_join_to_district, 
    caltrans_district
).pipe(
    add_segment_direction_vector
)

In [6]:
shapes = shapes.assign(
    road_length = shapes.geometry.length
)

shapes2 = cut_road_segments.cut_segments(
    shapes, 
    group_cols = ["shape_array_key"], 
    segment_length_meters = 50
).pipe(
    add_segment_direction_vector
).rename(columns = {"x_norm": "shape_x_norm", "y_norm": "shape_y_norm"})

In [7]:
shapes_buffered = buffer_shapes(shapes2, buffer_meters = 15)

In [8]:
s1 = gpd.sjoin(
    segmented_roads, 
    shapes_buffered[["shape_array_key", "shape_x_norm", "shape_y_norm", "geometry"]],
    how = "inner",
    predicate = "intersects"
).drop(columns = ["index_right"])

In [9]:
s1 = s1.assign(
    dot_product = geo_utils.dot_product(
        (s1.x_norm, s1.y_norm), (s1.shape_x_norm, s1.shape_y_norm))
)

In [10]:
dot_threshold = 0.65

s2 = s1[
    (s1.dot_product.abs () > dot_threshold)
][["linearid", "mtfcc", "fullname", "segment_sequence", 
   "shape_array_key", "geometry"]]

s3 = s2[["shape_array_key", "geometry"]].dissolve(by="shape_array_key").reset_index()

In [11]:
def plot_one_shape(s3, shapes2, one_shape):
    m = s3[(s3.shape_array_key == one_shape)
          ].explore(
        color="green", 
        tiles = "CartoDB Positron",
        name = "road segments"
    )

    m = shapes2[shapes2.shape_array_key==one_shape].explore(
        "shape_array_key", m=m, name = "shape"
    )

    folium.LayerControl().add_to(m)
    
    return m

In [12]:
# Plot every 3rd as a sample
for s in shapes2.shape_array_key.unique()[
    range(0, shapes2.shape_array_key.nunique(), 3)
]:
    my_map = plot_one_shape(s3, shapes2, s)
    print(s)
    display(my_map)

00e6dc43df4e1f7f717a4d00aa20937f


0666d32b5149fa57daf3467939a45cbc


0ce3b614f4cd4c033a593586f32a465d


11693bb10e7a428fa85fd78a1db6e37f


2978e049c9124cd5be92dc86b62b781e


...

dbad3506ec81d3ac39b130da081a814d


e25830f4a17f597b4b2105078d64dc41


e6a9a87acf81c1a9df7e3fbeaae40d87


f1bcad40e08f39481f5b42ede09af61f


ff57d040bcf49c50f3a5a66618544077
